# Step 2: Fit 7-9 Class GMMs and save class properties

This notebook will fit 7, 8 and 9 class GMMs to UK-ESM historical Southern Ocean data 2001-2018, following Jones et al. 2019 (https://doi.org/10.1029/2018JC014629). These models were trained in Step1_trainmodels.ipynb.

These files are required to reproduce figures 2, 3, 6, and 7 from *A Novel Heuristic Method for Detecting Overfit in Unsupervised Classification of Climate Models*, E. Boland et al. 2023 (doi to follow). This requires cluster_utils.py and input datafiles via the googleapi CMIP6 store (see cluster_utils.py for more info)

Outputs stored in \[model\]/\[ensemble\]/\[nclasses\]

Please attribute any plots or code from this notebook using the DOI from Zenodo: to come

Updated Mar 2023
E Atkinson & E Boland [emmomp@bas.ac.uk](email:emmomp@bas.ac.uk)

In [27]:
from dask.distributed import Client

client = Client("tcp://127.0.0.1:32978")
client

<Client: 'tcp://127.0.0.1:32978' processes=6 threads=6, memory=48.00 GiB>

2023-06-09 12:55:07,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.


In [26]:
from dask_gateway import Gateway
gateway = Gateway()
from dask.distributed import Client

'''properly shutdown any previous clusters'''
clusters=gateway.list_clusters()
if clusters != []:
    print(f'found {len(clusters)} clusters')
    for cluster in clusters:
        cluster = gateway.connect(cluster.name)
        client=Client(cluster)
        client.close()
        cluster.shutdown()

2023-06-09 12:54:22,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 12:54:27,767 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

In [28]:
import numpy as np
import xarray as xr

import os
import pickle

import cluster_utils as flt

### User options
Leave as is to recreate the paper

In [29]:
# Number of classes 
model='model'
classes = [7,8,9]
#Time range
tslice=slice('2001-01', '2017-12') 
#Depth range
levSel=slice(5, 2000)
#ids = ['r1i1p1f2', 'r2i1p1f2', 'r3i1p1f2', 'r4i1p1f2', 'r5i1p1f3', 'r6i1p1f3', 'r7i1p1f3', 'r8i1p1f2', 'r9i1p1f2', 'r10i1p1f2']
ids = ['r1i1p1f2', 'r2i1p1f2', 'r3i1p1f2', 'r4i1p1f2', 'r8i1p1f2', 'r16i1p1f2', 'r19i1p1f2']
mask = np.load('data/mask.npy', allow_pickle=True)

2023-06-09 12:55:12,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 12:55:17,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

In [22]:
avg_profiles = {}
m_id=ids[0]
n_classes=classes[0]
path_n = '{}/{}/{}'.format(model,m_id, n_classes)

print('Starting {}'.format(m_id))
options = {'memberId' : m_id}
path_id = '{}/{}'.format(model,m_id)

# Load PCA
with open('{}/pca.obj'.format(path_id),'rb') as file:
    pca=pickle.load(file)         

# Retrieve ALL Southern Ocean data
options = {'memberId' : m_id}
data = flt.retrieve_profiles(timeRange=tslice,mask=mask,options=options,levSel=levSel)
if tslice.stop>'2014-12':
    options['experimentId']='ssp370'
    data2 = flt.retrieve_profiles(timeRange=tslice,mask=mask,options=options,levSel=levSel)
    data=xr.concat([data,data2],'time')
data = data.chunk({'time': data.sizes['time'], 'n': 1024})

Starting r1i1p1f2


2023-06-09 12:10:37,767 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 12:10:42,765 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

In [23]:
data

<xarray.DataArray 'thetao' (time: 204, lev: 50, n: 22194)>
dask.array<rechunk-merge, shape=(204, 50, 22194), dtype=float32, chunksize=(204, 50, 1024), chunktype=numpy.ndarray>
Coordinates:
    lat      (n) float32 dask.array<chunksize=(1024,), meta=np.ndarray>
  * lev      (lev) float64 5.14 6.543 8.093 ... 1.653e+03 1.796e+03 1.945e+03
    lon      (n) float32 dask.array<chunksize=(1024,), meta=np.ndarray>
  * time     (time) datetime64[ns] 2001-01-01 2001-02-01 ... 2017-12-01
  * n        (n) MultiIndex
  - i        (n) int64 0 0 0 0 0 0 0 0 0 ... 359 359 359 359 359 359 359 359 359
  - j        (n) int64 81 82 83 84 85 86 87 88 ... 132 133 134 135 136 137 138
Attributes:
    cell_measures:  area: areacello volume: volcello
    cell_methods:   area: mean where sea time: mean
    comment:        mo: This variable is reported using a z* coordinate syste...
    long_name:      Sea Water Potential Temperature
    original_name:  mo: (variable_name: thetao)
    standard_name:  sea_water_potential_temperature
    units:          degC

2023-06-09 12:11:22,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 12:11:27,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

### Fit already trained models to full dataset and generate average profiles for chosen ensemble members and classes 

In [32]:
avg_profiles = {}
for m_id in ids:
    
    for nn,n_classes in enumerate(classes):   
        path_n = '{}/{}/{}'.format(model,m_id, n_classes)

        print('Starting {}'.format(m_id))
        options = {'memberId' : m_id}
        path_id = '{}/{}'.format(model,m_id)     
        
        # Load PCA
        with open('{}/pca.obj'.format(path_id),'rb') as file:
            pca=pickle.load(file)         
        
        # Retrieve ALL Southern Ocean data
        options = {'memberId' : m_id}
        data = flt.retrieve_profiles(timeRange=tslice,mask=mask,options=options,levSel=levSel)
        if tslice.stop>'2014-12':
            options['experimentId']='ssp370'
            data2 = flt.retrieve_profiles(timeRange=tslice,mask=mask,options=options,levSel=levSel)
            data=xr.concat([data,data2],'time')
        data = data.chunk({'time': data.sizes['time'], 'n': 1024})
        # Normalise the samples
        data_norm = flt.normalise_data(data, ('n', 'time')) 
        # Transform to PCA space
        data_trans = flt.pca_transform(data_norm, pca)
        print('Finished setup for {}'.format(m_id))      

        for nn,n_classes in enumerate(classes):  
            path_n = '{}/{}/{}'.format(model,m_id, n_classes)
            with open('{}/gmm.obj'.format(path_n),'rb') as file:
                gmm=pickle.load(file)                

            # Classify full dataset            
            print('Classifying full dataset into {} classes'.format(n_classes))
            data_classes = flt.gmm_classify(data_trans, gmm)
            data_probs = flt.gmm_prob(data_trans, gmm)
            print('Classification complete, writing to file'.format(n_classes))
            flt.write_tonc(data_classes.reset_index('n'),n_classes,m_id,'class',path_n)
            flt.write_tonc(data_probs.reset_index('n').mean('time'),n_classes,m_id,'probs',path_n)
            # Calculate average profiles for each class
            if os.path.isfile('{}/avg_prof.obj'.format(path_n)):
                continue
            else:
                # Calculate average profiles for each class
                avg_prof = flt.avg_profiles(data, data_classes, n_classes)
                print('Average profiles calculated, writing to file'.format(n_classes))
                with open('{}/avg_prof.obj'.format(path_n), 'wb') as file:
                    pickle.dump(avg_prof, file)      
            print('Done with {} classes'.format(n_classes))      
    
print('Done!')

Starting r1i1p1f2


2023-06-09 13:31:22,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 13:31:27,783 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

Finished setup for r1i1p1f2
Classifying full dataset into 7 classes
Classification complete, writing to file


2023-06-09 13:31:32,826 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 13:31:37,767 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

class written to model/r1i1p1f2/7/class.nc


...

probs written to model/r19i1p1f2/8/probs.nc
Classifying full dataset into 9 classes
Classification complete, writing to file


2023-06-09 23:02:22,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 23:02:27,826 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

class written to model/r19i1p1f2/9/class.nc


2023-06-09 23:03:32,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 23:03:37,826 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads

probs written to model/r19i1p1f2/9/probs.nc
Done!


In [30]:
avg_prof

[{'mean': array([7.229066 , 7.2267394, 7.2244306, 7.2220526, 7.2195315, 7.2167835,
         7.2137375, 7.210304 , 7.2063727, 7.2018027, 7.196403 , 7.1898947,
         7.181837 , 7.171538 , 7.158001 , 7.139821 , 7.11507  , 7.0815024,
         7.037057 , 6.980981 , 6.915069 , 6.844663 , 6.777433 , 6.7182336,
         6.6661654, 6.6176753, 6.5717077, 6.5278378, 6.484013 , 6.436924 ,
         6.381075 , 6.305478 , 6.197293 , 6.0438576, 5.8377514, 5.578718 ,
         5.2778277, 4.952211 , 4.619887 , 4.298408 , 4.0075126, 3.7602737,
         3.5595362, 3.396159 , 3.2554872, 3.1203666, 2.9801245, 2.830235 ,
         2.6654568, 2.4785178], dtype=float32),
  'std': array([1.6051997 , 1.6041781 , 1.6031657 , 1.6021284 , 1.6010329 ,
         1.5998454 , 1.5985365 , 1.5970714 , 1.5954113 , 1.5935061 ,
         1.591276  , 1.588584  , 1.5852119 , 1.5808241 , 1.5749542 ,
         1.5669376 , 1.5558317 , 1.5405676 , 1.5205574 , 1.4963385 ,
         1.4698807 , 1.4450834 , 1.42538   , 1.4109738 , 1.39

2023-06-09 12:56:47,767 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads=5, memory=40.00 GiB>>
Traceback (most recent call last):
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/tornado/ioloop.py", line 905, in _run
    return self.callback()
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/client.py", line 1339, in _heartbeat
    self.scheduler_comm.send({"op": "heartbeat-client"})
  File "/srv/conda/envs/notebook/lib/python3.9/site-packages/distributed/batched.py", line 140, in send
    raise CommClosedError(f"Comm {self.comm!r} already closed.")
distributed.comm.core.CommClosedError: Comm <TCP (closed) Client->Scheduler local=tcp://127.0.0.1:37228 remote=tcp://127.0.0.1:32937> already closed.
2023-06-09 12:56:52,766 - tornado.application - ERROR - Exception in callback <bound method Client._heartbeat of <Client: 'tcp://127.0.0.1:32937' processes=5 threads